In [3]:
import json
import pandas as pd
import numpy as np
import networkx as nx
import jellyfish
import os
import shutil
import subprocess
import requests
from github import Github
from git import Repo
from scipy.cluster.hierarchy import dendrogram, linkage
from matplotlib import pyplot as plt
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from sklearn.metrics import adjusted_rand_score
from sklearn import preprocessing
from sklearn.cluster import AgglomerativeClustering
from zipfile import ZipFile
from filecmp import dircmp
import configparser

In [4]:
config = configparser.ConfigParser()
config.read('authentication.ini')
print(config.sections())
github_oauth = config['github']['api_key']

['github']


In [5]:
g = Github(github_oauth, timeout=3000)
#g = Github()
repo = g.get_repo("square/okhttp")

In [26]:
print(g.get_rate_limit().core.remaining)
print(g.get_rate_limit().search.remaining)



5000
30


In [7]:
volatile_projects = pd.read_csv('volatile_projects.csv')

In [8]:
volatile_projects.head()

project_name                          project_link
0         Hive        https://github.com/apache/hive
1      Dbeaver    https://github.com/dbeaver/dbeaver
2        Camel       https://github.com/apache/camel
3     Redisson  https://github.com/redisson/redisson
4          Cxf         https://github.com/apache/cxf

In [27]:
main_arr = []

for row in volatile_projects.iterrows():
    
    repo = g.get_repo(row[1]['project_link'].replace('https://github.com/',''))
    count = 0
    for release in repo.get_tags():
        if count > 40:
            break
        
        try:
            temp_arr = []
            temp_arr.append(row[1]['project_name'])
            temp_arr.append(row[1]['project_link'])
            temp_arr.append(release.name)
            #temp_arr.append(release.commit)

            commit = repo.get_commit(sha=release.commit.sha)
            date = commit.commit.author.date

            print(release.name, commit, date)
            temp_arr.append(commit)
            temp_arr.append(date)

            main_arr.append(temp_arr)
        except:
            pass
        count += 1
    print(row[1]['project_name'], 'Success')

release-2.0.1 Commit(sha="e3cfeebcefe9a19c5055afdcbb00646908340694") 2016-05-04 04:02:05
release-2.0.0 Commit(sha="7f9f1fcb8697fb33f0edc2c391930a3728d247d7") 2016-02-10 01:53:25
release-1.2.1 Commit(sha="243e7c1ac39cb7ac8b65c5bc6988f5cc3162f558") 2015-06-19 08:49:55
release-1.2.0 Commit(sha="7f237de447bcd726bb3d0ba332cbb733f39fc02f") 2015-05-15 00:59:07
release-1.1.1 Commit(sha="3e8d832a1a8e2b12029adcb55862cf040098ef0f") 2015-05-14 22:09:06
release-1.1.0 Commit(sha="e60744d017ef79f1b17f474c0b969d4ca5592462") 2015-03-09 02:37:05
release-1.0.1 Commit(sha="73b600dc79ba8a9a32078a2ea0eb8ae3df20c9d5") 2015-05-14 21:54:45
release-1.0.0 Commit(sha="697aecadc3ba62bc11f3ba0a6c8522daeec7b53f") 2015-02-03 20:35:46
release-0.14.0 Commit(sha="70eea944afaf5f64b8939b2b3a0d8fdd33a41c18") 2014-11-12 20:35:15
release-0.13.1 Commit(sha="89bb2e8c34386b43efa37ecc6918a50c4bfb005f") 2014-06-05 21:03:32
release-0.13.0 Commit(sha="d0fe5f1b3ac361f747b12f9137322367da73652f") 2014-04-19 00:44:52
release-0.12.0 Com

camel-3.5.0 Commit(sha="62ef0198c65d95a55ce6e218cd49ba110fc9306c") 2020-08-31 12:21:58
camel-3.4.6 Commit(sha="78be7e5cb9bba7951bcb82689a9196efe1d3ca2b") 2021-06-17 12:49:47
camel-3.4.5 Commit(sha="4fd9cd8feb9dac66b8226b2c27742ed2e7825609") 2020-12-18 18:47:28
camel-3.4.4 Commit(sha="89937eb413852e07a13cf433150571c463a48a8e") 2020-09-22 11:30:28
camel-3.4.3 Commit(sha="54abda5aa2ede3878028e1270eb52ae278e6aa35") 2020-08-10 19:29:43
camel-3.4.2 Commit(sha="85f679b8ef5ff6f2de222741bc4512b7a52dfb12") 2020-07-18 21:54:47
camel-3.4.1 Commit(sha="e14a305b76b121c054596321c84d2adc18b33536") 2020-07-12 18:54:53
camel-3.4.0 Commit(sha="b665e5cf4b47f9b074bea40c86a5133f0db00454") 2020-06-14 13:52:37
camel-3.3.0 Commit(sha="7f96e2e248cc52a8d3c5899e50bbfe71427c69d4") 2020-05-10 18:40:29
camel-3.2.0 Commit(sha="77ae2991cd198ef1b5f4d6ac8c57bcba031f6d98") 2020-04-01 20:14:59
camel-3.1.0 Commit(sha="9636f69dd42c5b01052875f960fb05d2edc4a8a9") 2020-02-20 19:09:01
camel-3.0.1 Commit(sha="388fee27bb150b6cc05

cxf-3.2.9 Commit(sha="a00f4adfd418285720df7d6061e12cb198aa3225") 2019-05-10 12:52:35
cxf-3.2.8 Commit(sha="38dfa47141fbf36658ad8a9e35268edfe9642fd1") 2019-01-24 20:09:22
cxf-3.2.7 Commit(sha="d06235af319225cb081374041d723be937189d8c") 2018-10-24 17:10:40
cxf-3.2.6 Commit(sha="d3534eada388d2b07f10f83e35ca00c84eeb9801") 2018-08-08 21:20:01
cxf-3.2.5 Commit(sha="bc2f01b3c76266b9dd138ba33c226b303e33713d") 2018-06-18 18:55:29
cxf-3.2.4 Commit(sha="60b94b9c09b1eaf50516788b5c9c3573229d04f5") 2018-03-22 18:28:57
cxf-3.2.3 Commit(sha="b82303bfb6802817d3ce3be1ce30df74fee50675") 2018-03-16 19:08:03
cxf-3.2.2 Commit(sha="d579d7949d119dcf3d312059085bc200bcb3bbea") 2018-02-02 18:30:56
cxf-3.2.1 Commit(sha="dc2d22e374cb6adaabe0a963b73ca3d5c119f185") 2017-11-02 19:20:09
cxf-3.2.0 Commit(sha="f5ee3b786e22a081121eeebbba6d02fa9f4e7206") 2017-09-06 16:18:45
cxf-3.1.18 Commit(sha="7a26b733dc690cdd3e6186468c23a5397eedd6c5") 2019-01-25 13:35:28
cxf-3.1.17 Commit(sha="48fbcec621105ffae13404509b6433dcdba7c639"

release-3.0.1-RC0 Commit(sha="494d075055b52b0cc922bc25237e231bb3771c90") 2018-02-15 17:15:25
release-3.0.0-beta1-RC0 Commit(sha="1002c582d86ae8689c497c3d31b73f1ab92d5e29") 2017-09-28 18:32:31
release-3.0.0-alpha4-RC0 Commit(sha="e324cf8a2a6e55e996414ff281fee757f09d8172") 2017-06-30 00:58:38
release-3.0.0-alpha2-RC0 Commit(sha="1337ef4eef14fbbb214e71b68b7eb07061a4a212") 2017-01-20 18:43:28
release-3.0.0-alpha1-RC0 Commit(sha="a990d2ebcd6de5d7dc2d3684930759b0f0ea4dc3") 2016-08-30 05:23:40
release-3.0.0-RC1 Commit(sha="c25427ceca461ee979d30edd7a4b0f50718e6533") 2017-11-25 07:32:46
release-3.0.0-RC0 Commit(sha="3853c33466f7aad56f6981194d1810a42d10e02e") 2017-11-14 19:12:22
release-2.10.1-RC0 Commit(sha="1827467c9a56f133025f28557bfc2c562d78e816") 2018-03-08 17:23:45
release-2.10.0-RC1 Commit(sha="e2f1f118e465e787d8567dfa6e2f3b72a0eb9194") 2019-10-22 19:03:19
release-2.10.0-RC0 Commit(sha="1ee6d432f841fc5377327d38e657a615e50b06b5") 2019-10-16 00:21:45
Hadoop Success
v0.4-rc1 Commit(sha="0cc4

v2.1.2 Commit(sha="551baac08e4144475a6cdbba24e9b578773ff6f4") 2020-02-01 06:40:45
Alluxio Success
website-to-hugo Commit(sha="1d2700818474c008eaa324ac1b5c49c9d2857298") 2020-05-14 22:39:54
v2.31.0 Commit(sha="90f98a669d4819b469f25fd6f8d94c6a081c2b1a") 2021-06-21 19:56:23
v2.31.0-RC1 Commit(sha="90f98a669d4819b469f25fd6f8d94c6a081c2b1a") 2021-06-21 19:56:23
v2.30.0 Commit(sha="c026c9fa00239a6f3650a6fa69f3aa864f692afe") 2021-05-28 05:35:13
v2.30.0-RC1 Commit(sha="c026c9fa00239a6f3650a6fa69f3aa864f692afe") 2021-05-28 05:35:13
v2.29.0 Commit(sha="d7f44ed64351905c5b972921434da8100c142607") 2021-04-12 18:18:47
v2.29.0-RC1 Commit(sha="a467e2fc5e74a49fc3ae1fc8b371f818a4f715e9") 2021-04-15 20:20:49
v2.28.0 Commit(sha="4202efb5f01254e46fe421225a2ebbdba46da04d") 2021-02-13 18:40:51
v2.28.0-RC1 Commit(sha="4202efb5f01254e46fe421225a2ebbdba46da04d") 2021-02-13 18:40:51
v2.27.0 Commit(sha="ef9a640dd2860b0d1a630b1c11111876f8855528") 2021-01-06 03:50:30
v2.27.0-RC4 Commit(sha="ef9a640dd2860b0d1a630b1c

...

v1.3.3 Commit(sha="df56aaddabfa7b152c4586f0f11e54b4343d589e") 2020-04-29 14:08:54
v1.3.2 Commit(sha="dc692f57498b10e6f6c753a627dfbcd5fdd07905") 2020-04-15 20:01:03
v1.3.1 Commit(sha="79e4572f64c9bd50cefcbdb4874ecb9b5b99538d") 2020-04-08 18:29:04
v1.3.0 Commit(sha="6ae9608966306ad5477ef73c0c80859549e6c37f") 2020-04-08 12:10:59
v1.2.9 Commit(sha="956331d9c43e0d585f42b8105d510d303d35e1cc") 2020-03-16 13:55:06
v1.2.8 Commit(sha="94999670ecfb406f28d850090a3b5524c6b25561") 2020-03-10 17:18:59
v1.2.7 Commit(sha="1cb7b0521de0bdf090b6a61757714e7238967e3b") 2020-02-13 19:19:52
v1.2.6 Commit(sha="7f9c935a8b4ace6b6fdbbbdd6e62a85b61b738ba") 2020-02-12 16:58:22
v1.2.5 Commit(sha="31fd20ee136d9dbaa29a66cc45fc4f8214f3ab31") 2020-01-09 18:08:33
v1.2.4 Commit(sha="acd43507620ae31691f10690ccc2433118bc0f77") 2019-12-04 21:26:42
v1.2.3 Commit(sha="4521facce191d0b5d7d1542e9dfb58857a16f298") 2019-11-07 13:55:34
v1.2.2 Commit(sha="04777c4f2b9c6ab6d47bd903b7037920bef05ec7") 2019-11-01 08:03:16
Bisq Success
v1.

v2.2.0 Commit(sha="d464aa16d515c134f53c01c986d8fa09a87ec627") 2020-03-16 19:39:48
v2.1.0 Commit(sha="e0f8a7337a555d1ffa851fd585ca46d8e6f99342") 2019-11-08 11:12:58
v2.0.0 Commit(sha="49f9a756549ec0077bb28fdcf30f30106fdf8c73") 2019-06-13 13:13:00
v1.14.2 Commit(sha="99371abd6eb7d6d62e2fc9f799fd631c378244de") 2019-06-06 12:23:28
v1.14.0 Commit(sha="d08d1bf597bf91d646c2ebce788b5018f955b6ee") 2019-05-30 16:27:28
v1.13.0 Commit(sha="b59414a97b6fc37269985f6d8b111b756fc42464") 2019-02-21 11:37:19
v1.12.1 Commit(sha="4e2dc9ddb6d449d9850f193ad12504cd0a8cbc35") 2019-02-05 20:38:11
v1.12.0 Commit(sha="642b312856f582c9ceaba0a22f62ac3f89329b28") 2019-02-01 12:22:35
v1.11.0 Commit(sha="c60632332f8423e0f0998c444a31f3996eb4e948") 2018-10-11 14:58:32
v1.10.0 Commit(sha="2116559bad1dcd03b4a86be1c9863eb5685f6b8b") 2018-07-21 01:51:56
v1.9.0 Commit(sha="d14cbec7f559a5575702416fa4cb45e53a3af806") 2018-04-11 14:14:46
v1.8.1 Commit(sha="057aedb2fd1485a1849e8872105c427ea5bd380d") 2018-02-05 19:03:45
v1.8.0 Co

rel/avatica-1.11.0 Commit(sha="e533391b9acfb9623a0f00cb40937aee5aa7f2cd") 2018-03-06 03:44:34
rel/avatica-1.10.0 Commit(sha="fcec4be1368faa315bab18ed332c9ef9b85ba676") 2017-05-23 20:32:21
optiq-parent-0.8 Commit(sha="3da850a1988eb47665b9f2e7ce4096a8f0adb1d7") 2014-06-28 03:11:46
optiq-parent-0.7 Commit(sha="54a6e86958dbb464865833f6d71038a26afeb6fb") 2014-05-13 19:11:23
optiq-parent-0.6 Commit(sha="b6b31016d6532f1cdfd01206dcc71e685bec6f91") 2014-04-11 19:14:19
optiq-parent-0.5 Commit(sha="a1247e3e76fdd41e280f284687ae22ae86eb0b3b") 2014-03-14 07:10:27
optiq-parent-0.4.18.1 Commit(sha="4828bda63a1dc786348476cd4e75e06749ad50ee") 2014-02-20 20:26:57
optiq-parent-0.4.18 Commit(sha="13abd51f3e09f162c3a5e73d1f2fbad5d8a7f3be") 2014-02-15 07:51:09
optiq-parent-0.4.17 Commit(sha="17141312a7820efd52ab4d19d8d92d02af0043d5") 2014-01-14 00:57:32
optiq-parent-0.4.16 Commit(sha="0bf85074c89fb99f6b20993f37e56f3b9d4bd610") 2013-11-25 00:11:56
optiq-parent-0.4.15 Commit(sha="23cae05e4b016b1bdc71e6f6f772f4

powermock-2.0.0-RC.3 Commit(sha="a1bb65f7fbd2d88667e2390b4fc37cd2ed24e1fe") 2018-11-07 08:28:33
powermock-2.0.0-RC.2 Commit(sha="5e6bce0acaae83464293dad31c551e0a4bf9d1aa") 2018-10-28 21:05:13
powermock-2.0.0-RC.1 Commit(sha="3e0e26a1cea2299026a730038bb37e91f54fc513") 2018-10-24 20:44:57
powermock-1.7.4 Commit(sha="46a54bddaeedcd8d11287fa6055514694da2bb03") 2018-02-24 09:58:18
powermock-1.7.3 Commit(sha="e49955de8b73f71b8fa70145d54bfefb2ccd70bb") 2017-09-16 17:47:40
powermock-1.7.2 Commit(sha="42481482d4c39a472f6fca4ce4c61588da4ebe59") 2017-09-15 22:31:55
powermock-1.7.1 Commit(sha="4907b481a22e947efd7c8b89182a3a695ee08397") 2017-08-12 15:47:59
powermock-1.7.0 Commit(sha="3f951d23cb7131a178bde25a28c22cf4ed4e7020") 2017-06-15 15:15:05
powermock-1.7.0RC4 Commit(sha="f75b64f3b899f27ff2bc0914d89943f6ccf2788d") 2017-03-05 15:23:09
powermock-1.7.0RC2 Commit(sha="84131f9f9ebbeffcabac22fe4b5cf3bcb43fac0f") 2017-01-28 17:32:13
powermock-1.6.6 Commit(sha="76fe6f41883800497c425767ffdc51e7934f074f"

v2.0.0-rc1 Commit(sha="d9397fecfadc3e34ca8742b17077a3bac32624dd") 2019-04-18 18:40:23
Dropwizard Success
v2.5.0 Commit(sha="c83c733cbd86e0b8ff69c69e90aac0393fa9b26d") 2020-12-02 00:04:44
v2.4.1 Commit(sha="511718ef3aeadf6a96bc167bdfb04d6dda2091e6") 2019-11-29 16:55:57
v2.4.0 Commit(sha="7ba7249ce3fe62fee1b58b78ed238a6286a99d9f") 2019-03-02 00:37:47
v2.3.4 Commit(sha="ab0c4e535a9e7a40db54d2dcf4fdb24b63033f7f") 2018-09-05 23:31:58
v2.3.3 Commit(sha="b08fd5c91355de55effb5f6494c56f53828427f3") 2018-04-26 15:38:06
v2.3.2 Commit(sha="aff6354f5463dd79257a2850bc1615700dda8d7c") 2018-04-07 10:50:09
v2.3.1 Commit(sha="0e26950a722b0b4bea24610390545fc0376d9780") 2017-12-26 02:24:22
v2.3.0 Commit(sha="66ead001c6d9151968de22346c2618b0c1720fa2") 2017-09-21 10:38:54
v2.2.4 Commit(sha="045b7e7cc9ad3e2bc4fefc4cc43063dba019cc71") 2017-07-29 12:09:11
v2.2.3 Commit(sha="13ec3b6bfa5a606f6d3728a9298589fd3404d028") 2017-06-12 12:23:44
v2.2.2 Commit(sha="499c2f9039ba55c2bbc4ab7dc7b28c6e6cb78d92") 2017-01-22 16

In [28]:
new_links = pd.DataFrame(main_arr)
new_links.columns = ['project_name', 'project_link', 'version_name', 'commit', 'timestamp']
#new_links.columns = ['project_name', 'project_link','commit', 'timestamp']
new_links.head(15)

project_name                    project_link    version_name  \
0          Hive  https://github.com/apache/hive   release-2.0.1   
1          Hive  https://github.com/apache/hive   release-2.0.0   
2          Hive  https://github.com/apache/hive   release-1.2.1   
3          Hive  https://github.com/apache/hive   release-1.2.0   
4          Hive  https://github.com/apache/hive   release-1.1.1   
5          Hive  https://github.com/apache/hive   release-1.1.0   
6          Hive  https://github.com/apache/hive   release-1.0.1   
7          Hive  https://github.com/apache/hive   release-1.0.0   
8          Hive  https://github.com/apache/hive  release-0.14.0   
9          Hive  https://github.com/apache/hive  release-0.13.1   
10         Hive  https://github.com/apache/hive  release-0.13.0   
11         Hive  https://github.com/apache/hive  release-0.12.0   
12         Hive  https://github.com/apache/hive  release-0.11.0   
13         Hive  https://github.com/apache/hive  release-0.10.0   
14         Hive  https://github.com/apache/hive   release-0.9.0   

                                               commit           timestamp  
0   Commit(sha="e3cfeebcefe9a19c5055afdcbb00646908... 2016-05-04 04:02:05  
1   Commit(sha="7f9f1fcb8697fb33f0edc2c391930a3728... 2016-02-10 01:53:25  
2   Commit(sha="243e7c1ac39cb7ac8b65c5bc6988f5cc31... 2015-06-19 08:49:55  
3   Commit(sha="7f237de447bcd726bb3d0ba332cbb733f3... 2015-05-15 00:59:07  
4   Commit(sha="3e8d832a1a8e2b12029adcb55862cf0400... 2015-05-14 22:09:06  
5   Commit(sha="e60744d017ef79f1b17f474c0b969d4ca5... 2015-03-09 02:37:05  
6   Commit(sha="73b600dc79ba8a9a32078a2ea0eb8ae3df... 2015-05-14 21:54:45  
7   Commit(sha="697aecadc3ba62bc11f3ba0a6c8522daee... 2015-02-03 20:35:46  
8   Commit(sha="70eea944afaf5f64b8939b2b3a0d8fdd33... 2014-11-12 20:35:15  
9   Commit(sha="89bb2e8c34386b43efa37ecc6918a50c4b... 2014-06-05 21:03:32  
10  Commit(sha="d0fe5f1b3ac361f747b12f9137322367da... 2014-04-19 00:44:52  
11  Commit(sha="b77a6caafbba087bea617e87b566b5b55f... 2013-10-14 20:40:11  
12  Commit(sha="383fce63cb591359d27883be670d415575... 2013-05-16 03:40:10  
13  Commit(sha="7dde7825d80165e24497c6ae560407d4c0... 2013-01-10 18:02:52  
14  Commit(sha="51807a7aa6ba31644cdfd046e5d81e969e... 2012-04-27 21:33:09

In [29]:
len(new_links)

1908

In [31]:
new_links.to_csv('volatile_projects_complete_links_limit50.csv', index=False)

In [9]:
new_links['major_version'] = new_links['version_name'].apply(lambda x: x.split('.')[0])
new_links['major_version'] = new_links['major_version'].apply(lambda x: x.split('-')[-1])
new_links['major_version'] = new_links['major_version'].apply(lambda x: x.split('/')[-1])
new_links['major_version'] = new_links['major_version'].apply(lambda x: x.split('_')[-1])
new_links['major_version'] = new_links['major_version'].apply(lambda x: x.replace('v',''))
new_links['major_version'] = new_links['major_version'].apply(lambda x: x.replace('release',''))
new_links['major_version_int'] = pd.to_numeric(new_links['major_version'],errors='coerce')

In [10]:
new_links.head()

project_name                      project_link          version_name  \
0       okhttp  https://github.com/square/okhttp  parent-5.0.0-alpha.2   
1       okhttp  https://github.com/square/okhttp  parent-5.0.0-alpha.1   
2       okhttp  https://github.com/square/okhttp     parent-4.10.0-RC1   
3       okhttp  https://github.com/square/okhttp          parent-4.9.1   
4       okhttp  https://github.com/square/okhttp          parent-4.9.0   

                                              commit           timestamp  \
0  Commit(sha="b84627ef4bc43f2096c1b764720f9ff238... 2021-01-30 19:44:19   
1  Commit(sha="79d2a8d192d007b8acb2423d3ab6bba3a4... 2021-01-30 18:36:37   
2  Commit(sha="4fd1e8f99833eebdd2e99f3456322aa197... 2020-10-07 03:28:26   
3  Commit(sha="63dcd95bfa2345bb3f3d4abc6b6dbf36cf... 2021-01-30 18:09:57   
4  Commit(sha="cbeaf8f955fff9caa5652ccc6c1393ec8b... 2020-09-11 21:08:20   

  major_version  major_version_int  
0             5                5.0  
1             5                5.0  
2             4                4.0  
3             4                4.0  
4             4                4.0

In [11]:
cleaned_links = new_links.groupby(['project_name','major_version']).agg(['count']).reset_index()
cleaned_links.columns = cleaned_links.columns.droplevel()
cleaned_links.columns = ['project_name', 'major_version', 'count', 'count1', 'count2', 'count3', 'count4']
cleaned_links = cleaned_links[['project_name', 'major_version', 'count']]
cleaned_links.head()

project_name major_version  count
0       okhttp             1     14
1       okhttp             2     17
2       okhttp             3     48
3       okhttp             4     27
4       okhttp             5      2

In [12]:
cleaned_links_requirement_fulfill = cleaned_links[cleaned_links['count'] >= 20]
cleaned_links_requirement_fulfill = cleaned_links_requirement_fulfill.sort_values(['project_name', 'major_version'], ascending=False)
cleaned_links_requirement_fulfill = cleaned_links_requirement_fulfill[cleaned_links_requirement_fulfill['project_name'] != 'socketio-socket.io-client-java']
cleaned_links_requirement_fulfill = cleaned_links_requirement_fulfill[cleaned_links_requirement_fulfill['project_name'] != 'apache-sling-org-apache-sling-testing-sling-mock']
cleaned_links_requirement_fulfill = cleaned_links_requirement_fulfill[cleaned_links_requirement_fulfill['project_name'] != 'apache-sling-org-apache-sling-scripting-jsp']
cleaned_links_requirement_fulfill = cleaned_links_requirement_fulfill[cleaned_links_requirement_fulfill['project_name'] != 'apache-sling-org-apache-sling-resourceresolver']
cleaned_links_requirement_fulfill = cleaned_links_requirement_fulfill[cleaned_links_requirement_fulfill['project_name'] != 'apache-sling-org-apache-sling-event']
cleaned_links_requirement_fulfill['major_version'] = cleaned_links_requirement_fulfill['major_version'].apply(lambda x: x.split('-')[-1])
cleaned_links_requirement_fulfill['major_version'] = cleaned_links_requirement_fulfill['major_version'].apply(lambda x: x.split('/')[-1])
cleaned_links_requirement_fulfill['major_version'] = cleaned_links_requirement_fulfill['major_version'].apply(lambda x: x.split('_')[-1])
cleaned_links_requirement_fulfill['major_version'] = cleaned_links_requirement_fulfill['major_version'].apply(lambda x: x.replace('v',''))
cleaned_links_requirement_fulfill['major_version'] = cleaned_links_requirement_fulfill['major_version'].apply(lambda x: x.replace('r',''))
cleaned_links_requirement_fulfill['major_version'] = pd.to_numeric(cleaned_links_requirement_fulfill['major_version'])
cleaned_links_requirement_fulfill['count'] = cleaned_links_requirement_fulfill['count'].astype(str)
cleaned_links_requirement_fulfill['rank'] = cleaned_links_requirement_fulfill.groupby('project_name').rank(method='min',ascending=False)
cleaned_links_requirement_fulfill.head(5)

project_name  major_version count  rank
3       okhttp              4    27   1.0
2       okhttp              3    48   2.0

In [13]:
project_links_rank_1 = cleaned_links_requirement_fulfill[cleaned_links_requirement_fulfill['rank'] == 1]
project_links_rank_1['major_version_int'] = project_links_rank_1['major_version']
project_links_rank_1.head()

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


project_name  major_version count  rank  major_version_int
3       okhttp              4    27   1.0                  4

In [14]:
final_links = pd.merge(new_links, project_links_rank_1, how='right', on=['project_name', 'major_version_int'])
final_links.tail()

project_name                      project_link          version_name  \
22       okhttp  https://github.com/square/okhttp  parent-4.0.0-alpha02   
23       okhttp  https://github.com/square/okhttp      parent-4.0.0-RC3   
24       okhttp  https://github.com/square/okhttp      parent-4.0.0-RC2   
25       okhttp  https://github.com/square/okhttp      parent-4.0.0-RC1   
26       okhttp  https://github.com/square/okhttp  parent-4.0.0-ALPHA01   

                                               commit           timestamp  \
22  Commit(sha="7925bfc5c5da1605486e37a9360ab03f1e... 2019-05-26 00:53:59   
23  Commit(sha="bad333c0a31904ff76b0d67ab8c46d085c... 2019-06-24 23:44:19   
24  Commit(sha="8603e2d20e4335a7a530f90a2f6439d16b... 2019-06-21 14:01:40   
25  Commit(sha="148938a17895ec72ee09b6bb4d23fb2bd7... 2019-06-04 04:28:50   
26  Commit(sha="8f21b934f928986bba7e50114911c3c494... 2019-05-09 00:54:28   

   major_version_x  major_version_int  major_version_y count  rank  
22               4                4.0                4    27   1.0  
23               4                4.0                4    27   1.0  
24               4                4.0                4    27   1.0  
25               4                4.0                4    27   1.0  
26               4                4.0                4    27   1.0

In [15]:
final_20limit_links = final_links.groupby('project_name').head(20)

In [16]:
final_20limit_links.to_csv('volatile_projects_complete_links_limit20.csv', index=False)

## Skip the following 2 cells for full run

In [5]:
project_name = 'okhttp'
project_releases = pd.read_csv('volatile_projects_complete_links_limit20.csv')

#project_releases = project_releases[project_releases['project_name'] == 'apache-spark']

In [6]:
current_project = pd.DataFrame(project_releases[project_releases['project_name'] == project_name])
current_project['rank'] = current_project['timestamp'].rank()
current_project = current_project.sort_values(by=['rank'], ascending=False)
current_project['previous_version'] = current_project['version_name'].shift(-1)
current_project['previous_version_timestamp'] = current_project['timestamp'].shift(-1)
current_project['previous_version_timestamp'].fillna(current_project['timestamp'], inplace=True)
current_project['timestamp']= pd.to_datetime(current_project['timestamp'])
current_project['previous_version_timestamp']= pd.to_datetime(current_project['previous_version_timestamp'])
current_project['timestamp_diff'] = current_project['timestamp'] - current_project['previous_version_timestamp']
current_project['timestamp_diff_hours'] = current_project['timestamp_diff'].astype('timedelta64[h]')
current_project.tail()

project_name                      project_link  version_name  \
15       okhttp  https://github.com/square/okhttp  parent-4.2.2   
16       okhttp  https://github.com/square/okhttp  parent-4.2.1   
17       okhttp  https://github.com/square/okhttp  parent-4.2.0   
18       okhttp  https://github.com/square/okhttp  parent-4.1.1   
19       okhttp  https://github.com/square/okhttp  parent-4.1.0   

                                               commit           timestamp  \
15  Commit(sha="d02340f9dfac4ead42befc1a4d477b4540... 2019-10-06 20:18:49   
16  Commit(sha="57a165b69c6551c1caec8a557e0e9c9abf... 2019-10-02 12:53:27   
17  Commit(sha="582f8ef2f78cf001d479cb65831674289f... 2019-09-10 17:04:12   
18  Commit(sha="cf93aca33cc30a44724a8fb9e7042ccd17... 2019-09-05 04:24:05   
19  Commit(sha="4739b278066c25de7d1fcada943e0aaddd... 2019-08-12 17:00:00   

    major_version_x  major_version_int  major_version_y  count  rank  \
15                4                4.0                4     27   5.0   
16                4                4.0                4     27   4.0   
17                4                4.0                4     27   3.0   
18                4                4.0                4     27   2.0   
19                4                4.0                4     27   1.0   

   previous_version previous_version_timestamp   timestamp_diff  \
15     parent-4.2.1        2019-10-02 12:53:27  4 days 07:25:22   
16     parent-4.2.0        2019-09-10 17:04:12 21 days 19:49:15   
17     parent-4.1.1        2019-09-05 04:24:05  5 days 12:40:07   
18     parent-4.1.0        2019-08-12 17:00:00 23 days 11:24:05   
19              NaN        2019-08-12 17:00:00  0 days 00:00:00   

    timestamp_diff_hours  
15                 103.0  
16                 523.0  
17                 132.0  
18                 563.0  
19                   0.0

In [19]:
### Download dataset
try:
    os.mkdir('raw_sourcecode/' + project_name)
except:
    pass
for row in current_project.iterrows():
    command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/' + project_name +' & mkdir ' + project_name + '_' +row[1]['version_name']
    
    #print(command)
    os.system(command)
    
    command = 'git clone ' + row[1]['project_link'] +  ' C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/' + project_name + '/' + project_name + '_' + row[1]['version_name']
    
    print(command)
    os.system(command)
    commit = row[1]['commit'].replace('Commit(sha="','')
    commit = commit.replace('")','')
    command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/' + project_name + '/' + project_name +'_' + row[1]['version_name'] + ' & git checkout ' + commit
    print(command)
    os.system(command)

git clone https://github.com/square/okhttp C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.1
cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.1 & git checkout 63dcd95bfa2345bb3f3d4abc6b6dbf36cfb08aaf
git clone https://github.com/square/okhttp C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.10.0-RC1
cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.10.0-RC1 & git checkout 4fd1e8f99833eebdd2e99f3456322aa197f5e652
git clone https://github.com/square/okhttp C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.0
cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.0 & git checkout cbeaf8f955fff9caa5652ccc6c1393ec8b993799
git clone https://github.com/square/okhttp C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.8.1
cd C:/Users

In [20]:
### Run Depends
try:
    os.mkdir('raw_depends/' + project_name)
except:
    pass
for row in current_project.iterrows():
    #command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_depends/' + project_name +' & mkdir ' + project_name + '_' +row[1]['version_name']
    #os.system(command)
    #print(command)
    command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/depends-0.9.2 & ' + 'java -jar depends.jar java C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/'  + project_name + '/' + project_name + '_' + row[1]['version_name']+  ' ../raw_depends/' + project_name + "/" + project_name + '_' + row[1]['version_name'] 
    print(command)
    os.system(command)

cd C:/Users/tanji/Desktop/SoftwareRemodularization/depends-0.9.2 & java -jar depends.jar java C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.1 ../raw_depends/okhttp/okhttp_parent-4.9.1
cd C:/Users/tanji/Desktop/SoftwareRemodularization/depends-0.9.2 & java -jar depends.jar java C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.10.0-RC1 ../raw_depends/okhttp/okhttp_parent-4.10.0-RC1
cd C:/Users/tanji/Desktop/SoftwareRemodularization/depends-0.9.2 & java -jar depends.jar java C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.0 ../raw_depends/okhttp/okhttp_parent-4.9.0
cd C:/Users/tanji/Desktop/SoftwareRemodularization/depends-0.9.2 & java -jar depends.jar java C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.8.1 ../raw_depends/okhttp/okhttp_parent-4.8.1
cd C:/Users/tanji/Desktop/SoftwareRemodularization/depends-0.9.2 & java -jar depends.j

In [21]:
### Generate groundtruth
try:
    os.mkdir('groundtruth/' + project_name)
except:
    pass

counter = 10
for row in current_project.iterrows():
    counter -= 1
    if counter < 0:
        break
    project_rank = row[1]['rank']
    version_name = row[1]['version_name']
    #print(project_rank)
    rootdir = 'C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/' + project_name + '/' + project_name + '_' + row[1]['version_name']

    print(rootdir, 'current_project')


    ### To obtain the current initial directory
    full_dir_arr = []
    for root, dirs, files in os.walk(rootdir):
        #print(root)
        #print(dirs)
        for element in files:
            if '.java' in element:
                dir_string = root + '\\' + element
                full_dir_arr.append(dir_string)

    cluster_dict = {}
    cluster_tree = {}


    for element in full_dir_arr:
        element = element.split('\\')
        child = element[-1]
        parent = element[-2]
        cluster_tree[child] = parent
    

    '''
    current_rank = project_rank
    try:
        while current_rank >= (project_rank - 9):
            current_rank -= 1
            project_to_be_compared = current_project[current_project['rank'] == current_rank]
            project_to_be_compared_rootdir = 'C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/' + project_name + '/' + project_name + '_' + project_to_be_compared['version_name'].values[0]
            #print(project_to_be_compared_rootdir)


            ### To obtain the current initial directory
            project_to_be_compared_full_dir_arr = []
            for root, dirs, files in os.walk(project_to_be_compared_rootdir):
                #print(root)
                #print(dirs)
                for element in files:
                    if '.java' in element:
                        dir_string = root + '\\' + element
                        project_to_be_compared_full_dir_arr.append(dir_string)

            project_to_be_compared_cluster_dict = {}
            project_to_be_compared_cluster_tree = {}


            for element in project_to_be_compared_full_dir_arr:
                element = element.split('\\')
                child = element[-1]
                parent = element[-2]
                project_to_be_compared_cluster_tree[child] = parent

            cluster_tree =  {x:cluster_tree[x] for x in cluster_tree if x in project_to_be_compared_cluster_tree} 
    '''
    arr_a_rsf = []
    filename = 'C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/' + project_name + '/' + project_name + '_' + row[1]['version_name'] + '.txt'
    with open(filename, 'w') as f:
        for key, value in cluster_tree.items():
            arr_a_rsf.append(key)
            f.write('contain ' + str(value).replace(" ",'') + ' ' + str(key).replace(' ','') + '\n')

        #depends_dir = 'C:/Users/tanji/Desktop/SoftwareRemodularization/raw_depends/' + project_name + '/' + project_name + '_' + row[1]['version_name'] + '.json'
        #print(depends_dir)
    #except:
        #print(e)
        #pass
    
        
        

C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.1 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.10.0-RC1 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.0 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.8.1 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.8.0 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.7.2 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.7.1 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.7.0 current_project
C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.6.0 current_project
C:/Users/tanji/Desktop/SoftwareRemodulari

In [27]:
current_project.head()

project_name                      project_link       version_name  \
1       okhttp  https://github.com/square/okhttp       parent-4.9.1   
0       okhttp  https://github.com/square/okhttp  parent-4.10.0-RC1   
2       okhttp  https://github.com/square/okhttp       parent-4.9.0   
3       okhttp  https://github.com/square/okhttp       parent-4.8.1   
4       okhttp  https://github.com/square/okhttp       parent-4.8.0   

                                              commit           timestamp  \
1  Commit(sha="63dcd95bfa2345bb3f3d4abc6b6dbf36cf... 2021-01-30 18:09:57   
0  Commit(sha="4fd1e8f99833eebdd2e99f3456322aa197... 2020-10-07 03:28:26   
2  Commit(sha="cbeaf8f955fff9caa5652ccc6c1393ec8b... 2020-09-11 21:08:20   
3  Commit(sha="fc6c29c4f93a7604fb0fee88be4bbc91dd... 2020-08-06 14:01:19   
4  Commit(sha="a70e992c3f7d9adea544c40cc2a4640d28... 2020-07-11 18:01:06   

   major_version_x  major_version_int  major_version_y  count  rank  \
1                4                4.0                4     27  20.0   
0                4                4.0                4     27  19.0   
2                4                4.0                4     27  18.0   
3                4                4.0                4     27  17.0   
4                4                4.0                4     27  16.0   

    previous_version previous_version_timestamp    timestamp_diff  \
1  parent-4.10.0-RC1        2020-10-07 03:28:26 115 days 14:41:31   
0       parent-4.9.0        2020-09-11 21:08:20  25 days 06:20:06   
2       parent-4.8.1        2020-08-06 14:01:19  36 days 07:07:01   
3       parent-4.8.0        2020-07-11 18:01:06  25 days 20:00:13   
4       parent-4.7.2        2020-05-20 13:06:47  52 days 04:54:19   

   timestamp_diff_hours  
1                2774.0  
0                 606.0  
2                 871.0  
3                 620.0  
4                1252.0

In [23]:
### Run Refactoring Miner

project_name
#print(current_project.head())
first_tag = current_project.head(1)['version_name'].values[0]
last_tag= current_project.tail(1)['version_name'].values[0]

print(first_tag)
print(last_tag)

try:
    os.mkdir('raw_refactoringMiner/' + project_name)
except:
    pass
try:
    for row in current_project.iterrows():
        #command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/raw_depends/' + project_name +' & mkdir ' + project_name + '_' +row[1]['version_name']
        #os.system(command)
        #print(command)
        command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/RefactoringMiner-2.1.0/bin & ' + 'RefactoringMiner -bt C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/'  + project_name + '/' + project_name + '_' + row[1]['version_name'] + ' ' + row[1]['previous_version'] + ' ' + row[1]['version_name'] + ' -json ' + 'C:/Users/tanji/Desktop/SoftwareRemodularization/raw_refactoringMiner/' +project_name + '/'+ project_name + '_' + row[1]['version_name'] + '.json'
        print(command)
        os.system(command)
except:
    pass



parent-4.9.1
parent-4.1.0
cd C:/Users/tanji/Desktop/SoftwareRemodularization/RefactoringMiner-2.1.0/bin & RefactoringMiner -bt C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.1 parent-4.10.0-RC1 parent-4.9.1 -json C:/Users/tanji/Desktop/SoftwareRemodularization/raw_refactoringMiner/okhttp/okhttp_parent-4.9.1.json
cd C:/Users/tanji/Desktop/SoftwareRemodularization/RefactoringMiner-2.1.0/bin & RefactoringMiner -bt C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.10.0-RC1 parent-4.9.0 parent-4.10.0-RC1 -json C:/Users/tanji/Desktop/SoftwareRemodularization/raw_refactoringMiner/okhttp/okhttp_parent-4.10.0-RC1.json
cd C:/Users/tanji/Desktop/SoftwareRemodularization/RefactoringMiner-2.1.0/bin & RefactoringMiner -bt C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/okhttp/okhttp_parent-4.9.0 parent-4.8.1 parent-4.9.0 -json C:/Users/tanji/Desktop/SoftwareRemodularization/raw_refactoringMiner/okhttp/okhttp_

In [28]:
current_project.head()

project_name                      project_link       version_name  \
1       okhttp  https://github.com/square/okhttp       parent-4.9.1   
0       okhttp  https://github.com/square/okhttp  parent-4.10.0-RC1   
2       okhttp  https://github.com/square/okhttp       parent-4.9.0   
3       okhttp  https://github.com/square/okhttp       parent-4.8.1   
4       okhttp  https://github.com/square/okhttp       parent-4.8.0   

                                              commit           timestamp  \
1  Commit(sha="63dcd95bfa2345bb3f3d4abc6b6dbf36cf... 2021-01-30 18:09:57   
0  Commit(sha="4fd1e8f99833eebdd2e99f3456322aa197... 2020-10-07 03:28:26   
2  Commit(sha="cbeaf8f955fff9caa5652ccc6c1393ec8b... 2020-09-11 21:08:20   
3  Commit(sha="fc6c29c4f93a7604fb0fee88be4bbc91dd... 2020-08-06 14:01:19   
4  Commit(sha="a70e992c3f7d9adea544c40cc2a4640d28... 2020-07-11 18:01:06   

   major_version_x  major_version_int  major_version_y  count  rank  \
1                4                4.0                4     27  20.0   
0                4                4.0                4     27  19.0   
2                4                4.0                4     27  18.0   
3                4                4.0                4     27  17.0   
4                4                4.0                4     27  16.0   

    previous_version previous_version_timestamp    timestamp_diff  \
1  parent-4.10.0-RC1        2020-10-07 03:28:26 115 days 14:41:31   
0       parent-4.9.0        2020-09-11 21:08:20  25 days 06:20:06   
2       parent-4.8.1        2020-08-06 14:01:19  36 days 07:07:01   
3       parent-4.8.0        2020-07-11 18:01:06  25 days 20:00:13   
4       parent-4.7.2        2020-05-20 13:06:47  52 days 04:54:19   

   timestamp_diff_hours  
1                2774.0  
0                 606.0  
2                 871.0  
3                 620.0  
4                1252.0

# Remember to replace file path here accordingly

C:\\Users\\tanji\\Desktop\\SoftwareRemodularization\\raw_sourcecode\\

In [3]:
print(depends_filename)
with open(depends_filename) as f:
    depends_results = json.load(f)
    index  = 0
    var_array = []
    for value in depends_results['variables']:
        file_path = value.replace('\\','/')
        file_path = file_path.replace('C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/' + project_name + '/', '')
        #var_array.append([index, value.replace('\\','/')])
        #var_array.append([index,file_path])
        var_array.append(file_path)
        #var_array.append([index, value.split('\\')[-1]])
        #print(index, value)
        index += 1

    #var_df = pd.DataFrame(var_array)
    #var_df.columns = ['index_val', 'name']

    feature_list = {}
    feature_index = 2
    for element in depends_results['cells']:
        #print(element)
        try:
            for a in element['values']:
                if a not in feature_list:
                    feature_list[a] = feature_index
                    feature_index += 1
                #print(a['Call'])


        except:
            pass

    feature_arr = []
    for element in depends_results['cells']:
        #print(array)
        array = [0] * (len(feature_list) + 2)
        values = dict(element['values'])
        #print(element)
        array[0] = element['src']
        array[1] = element['dest']
        for feature in feature_list:
            try:
                value = values[feature]
                array[feature_list[feature]] = value
            except:
                pass
        #print(array)
        feature_arr.append(array)

    feature_df = pd.DataFrame(feature_arr)
    col_names = ['src', 'dest']
    for element in feature_list:
        col_names.append(element)
    feature_df.columns = col_names

    feature_df['sum'] = feature_df.sum(axis=1) - feature_df['src'] - feature_df['dest']
    
G = nx.Graph()
for index, row in feature_df.iterrows():
    G.add_edge(row['src'], row['dest'], weight=row['sum'])

sum_dependency_df = nx.to_pandas_adjacency(G)
sum_dependency_df['sum'] = sum_dependency_df.sum(axis=1)
#sum_dependency_df
final_dependency_df = sum_dependency_df['sum']
    
#adj_mat = nx.adjacency_matrix(G,weight='weight')
#adj_mat_df = pd.DataFrame(adj_mat.todense())
#np.fill_diagonal(adj_mat_df.values, adj_mat_df.values.max())
#x = adj_mat_df.values
#min_max_scaler = preprocessing.MinMaxScaler()
#x_scaled = min_max_scaler.fit_transform(x)
#adj_mat_df = pd.DataFrame(x)
#adj_mat_df

NameError: name 'depends_filename' is not defined

In [70]:
test = nx.to_pandas_adjacency(G)
test['sum'] = test.sum(axis=1)
test

146.0  145.0  142.0  29.0  91.0  74.0  39.0  84.0  88.0  10.0  ...  \
146.0    0.0    4.0    4.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
145.0    4.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
142.0    4.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
29.0     0.0    0.0    0.0   0.0   9.0   0.0   0.0   0.0   0.0   0.0  ...   
91.0     0.0    0.0    0.0   9.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
...      ...    ...    ...   ...   ...   ...   ...   ...   ...   ...  ...   
43.0     0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
58.0     0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
77.0     0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
72.0     0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  ...   
96.0     0.0    0.0    0.0   0.0   0.0   0.0   4.0   0.0   0.0   0.0  ...   

       67.0  68.0  69.0  44.0  43.0  58.0  77.0  72.0  96.0    sum  
146.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   25.0  
145.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    6.0  
142.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   13.0  
29.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  321.0  
91.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   33.0  
...     ...   ...   ...   ...   ...   ...   ...   ...   ...    ...  
43.0    0.0   0.0   0.0   0.0   0.0   3.0   0.0   0.0   0.0   14.0  
58.0    0.0   0.0   0.0   0.0   3.0   0.0   0.0   0.0   0.0    3.0  
77.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    3.0  
72.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   29.0  
96.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0    4.0  

[65 rows x 66 columns]

In [98]:
file_dict

{'mockwebserver/src/test/java/okhttp3/mockwebserver/CustomDispatcherTest.java': 0,
 'mockwebserver/src/test/java/okhttp3/mockwebserver/MockWebServerTest.java': 1,
 'mockwebserver/src/test/java/okhttp3/mockwebserver/RecordedRequestTest.java': 2,
 'mockwebserver/src/test/java/okhttp3/mockwebserver/internal/http2/Http2Server.java': 3,
 'okcurl/src/test/java/okhttp3/curl/MainTest.java': 4,
 'okhttp-brotli/src/test/java/okhttp3/brotli/BrotliInterceptorJavaApiTest.java': 5,
 'okhttp-dnsoverhttps/src/test/java/okhttp3/dnsoverhttps/DnsOverHttpsTest.java': 6,
 'okhttp-dnsoverhttps/src/test/java/okhttp3/dnsoverhttps/DnsRecordCodecTest.java': 7,
 'okhttp-dnsoverhttps/src/test/java/okhttp3/dnsoverhttps/DohProviders.java': 8,
 'okhttp-dnsoverhttps/src/test/java/okhttp3/dnsoverhttps/TestDohMain.java': 9,
 'okhttp-hpacktests/src/test/java/okhttp3/internal/http2/HpackDecodeInteropTest.java': 10,
 'okhttp-hpacktests/src/test/java/okhttp3/internal/http2/HpackDecodeTestBase.java': 11,
 'okhttp-hpacktests

In [99]:
file_dict['okhttp-sse/src/test/java/okhttp3/internal/sse/Event.java']

KeyError: 'okhttp-sse/src/test/java/okhttp3/internal/sse/Event.java'

In [10]:
current_project.head()

project_name                      project_link       version_name  \
1       okhttp  https://github.com/square/okhttp       parent-4.9.1   
0       okhttp  https://github.com/square/okhttp  parent-4.10.0-RC1   
2       okhttp  https://github.com/square/okhttp       parent-4.9.0   
3       okhttp  https://github.com/square/okhttp       parent-4.8.1   
4       okhttp  https://github.com/square/okhttp       parent-4.8.0   

                                              commit           timestamp  \
1  Commit(sha="63dcd95bfa2345bb3f3d4abc6b6dbf36cf... 2021-01-30 18:09:57   
0  Commit(sha="4fd1e8f99833eebdd2e99f3456322aa197... 2020-10-07 03:28:26   
2  Commit(sha="cbeaf8f955fff9caa5652ccc6c1393ec8b... 2020-09-11 21:08:20   
3  Commit(sha="fc6c29c4f93a7604fb0fee88be4bbc91dd... 2020-08-06 14:01:19   
4  Commit(sha="a70e992c3f7d9adea544c40cc2a4640d28... 2020-07-11 18:01:06   

   major_version_x  major_version_int  major_version_y  count  rank  \
1                4                4.0                4     27  20.0   
0                4                4.0                4     27  19.0   
2                4                4.0                4     27  18.0   
3                4                4.0                4     27  17.0   
4                4                4.0                4     27  16.0   

    previous_version previous_version_timestamp    timestamp_diff  \
1  parent-4.10.0-RC1        2020-10-07 03:28:26 115 days 14:41:31   
0       parent-4.9.0        2020-09-11 21:08:20  25 days 06:20:06   
2       parent-4.8.1        2020-08-06 14:01:19  36 days 07:07:01   
3       parent-4.8.0        2020-07-11 18:01:06  25 days 20:00:13   
4       parent-4.7.2        2020-05-20 13:06:47  52 days 04:54:19   

   timestamp_diff_hours  
1                2774.0  
0                 606.0  
2                 871.0  
3                 620.0  
4                1252.0

In [13]:
counter = 1
main_data_arr = []

for row in current_project.iterrows():
    
    refactoring_miner_filename = f'raw_refactoringMiner/{project_name}/' + project_name + '_' + row[1]['version_name'] + '.json'
    depends_filename = f'raw_depends/{project_name}/' + project_name + '_' + row[1]['version_name'] + '.json'
    latest_commit = row[1]['commit'].replace('Commit(sha="','')
    latest_commit = latest_commit.replace('")','')
    print(latest_commit)
    print(refactoring_miner_filename)
    
    print(depends_filename)
    with open(depends_filename) as f:
        depends_results = json.load(f)
        index  = 0
        file_dict = {}
        for value in depends_results['variables']:
            file_path = value.replace('\\','/')
            string = f"C:/Users/tanji/Desktop/SoftwareRemodularization/raw_sourcecode/{project_name}/{project_name}_{row[1]['version_name']}/"
            #print(string)
            file_path = file_path.replace(string, '')
            #var_array.append([index, value.replace('\\','/')])
            #var_array.append([index,file_path])
            file_dict[file_path] = index
            #var_array.append(file_path)
            #var_array.append([index, value.split('\\')[-1]])
            #print(index, value)
            index += 1

        #var_df = pd.DataFrame(var_array)
        #var_df.columns = ['index_val', 'name']
        #var_df = var_df.set_index('name')

        feature_list = {}
        feature_index = 2
        for element in depends_results['cells']:
            #print(element)
            try:
                for a in element['values']:
                    if a not in feature_list:
                        feature_list[a] = feature_index
                        feature_index += 1
                    #print(a['Call'])


            except:
                pass

        feature_arr = []
        for element in depends_results['cells']:
            #print(array)
            array = [0] * (len(feature_list) + 2)
            values = dict(element['values'])
            #print(element)
            array[0] = element['src']
            array[1] = element['dest']
            for feature in feature_list:
                try:
                    value = values[feature]
                    array[feature_list[feature]] = value
                except:
                    pass
            #print(array)
            feature_arr.append(array)

        feature_df = pd.DataFrame(feature_arr)
        col_names = ['src', 'dest']
        for element in feature_list:
            col_names.append(element)
        feature_df.columns = col_names

        feature_df['sum'] = feature_df.sum(axis=1) - feature_df['src'] - feature_df['dest']

    G = nx.Graph()
    for index, row in feature_df.iterrows():
        G.add_edge(row['src'], row['dest'], weight=row['sum'])

    sum_dependency_df = nx.to_pandas_adjacency(G)
    sum_dependency_df['sum'] = sum_dependency_df.sum(axis=1)
    #sum_dependency_df
    final_dependency_df = sum_dependency_df['sum']
    
    
    
    try:
        f = open(refactoring_miner_filename)
    except:
        break
    refactoring_miner = json.load(f)
    for i in refactoring_miner['commits']:
                
        if len(i['refactorings']) != 0:
            commit_compared_with = i['sha1']
            file_arr = []
            num_line_affected = 0
            num_dependency = 0
            actual_num_of_classes_touched = 0
            for refactor in i['refactorings']:
                #print(refactor)
                for file in refactor['leftSideLocations']:
                    try:
                        #file_arr.append(file['filePath'])
                        #print(file['filePath'], 'here')
                        #print(file_dict[file['filePath']])
                        actual_num_of_classes_touched += 1
                        num_dependency += final_dependency_df[file_dict[file['filePath']]]
                        num_line_affected += file['endLine'] - file['startLine']
                    except:
                        pass 
            if num_dependency != 0 and num_line_affected != 0:
                main_data_arr.append([latest_commit, commit_compared_with, num_dependency, num_line_affected, actual_num_of_classes_touched])
                    
                    
            
            #print(i)
    f.close()
    counter += 1
effort_data_df = pd.DataFrame(main_data_arr)
effort_data_df.columns = ['latest_commit', 'commit_compared_with', 'num_dependency', 'num_line_affected', 'actual_num_of_classes_touched']
effort_data_df

63dcd95bfa2345bb3f3d4abc6b6dbf36cfb08aaf
raw_refactoringMiner/okhttp/okhttp_parent-4.9.1.json
raw_depends/okhttp/okhttp_parent-4.9.1.json
4fd1e8f99833eebdd2e99f3456322aa197f5e652
raw_refactoringMiner/okhttp/okhttp_parent-4.10.0-RC1.json
raw_depends/okhttp/okhttp_parent-4.10.0-RC1.json
cbeaf8f955fff9caa5652ccc6c1393ec8b993799
raw_refactoringMiner/okhttp/okhttp_parent-4.9.0.json
raw_depends/okhttp/okhttp_parent-4.9.0.json
fc6c29c4f93a7604fb0fee88be4bbc91dde6551d
raw_refactoringMiner/okhttp/okhttp_parent-4.8.1.json
raw_depends/okhttp/okhttp_parent-4.8.1.json
a70e992c3f7d9adea544c40cc2a4640d28f45cc3
raw_refactoringMiner/okhttp/okhttp_parent-4.8.0.json
raw_depends/okhttp/okhttp_parent-4.8.0.json
4c595553fbcbfc316d24a74197aa753dbc05da9f
raw_refactoringMiner/okhttp/okhttp_parent-4.7.2.json
raw_depends/okhttp/okhttp_parent-4.7.2.json
186ec88aff706f31724210f0b73f88e942e7fb11
raw_refactoringMiner/okhttp/okhttp_parent-4.7.1.json
raw_depends/okhttp/okhttp_parent-4.7.1.json
ef7c5f358e2ac8dad806952c

latest_commit  \
0   cbeaf8f955fff9caa5652ccc6c1393ec8b993799   
1   ef7c5f358e2ac8dad806952c70c7af9061a6f7af   
2   ef7c5f358e2ac8dad806952c70c7af9061a6f7af   
3   ef7c5f358e2ac8dad806952c70c7af9061a6f7af   
4   7334150d1da63f4fe7e256de173bdc5837022ff9   
5   7334150d1da63f4fe7e256de173bdc5837022ff9   
6   7334150d1da63f4fe7e256de173bdc5837022ff9   
7   7334150d1da63f4fe7e256de173bdc5837022ff9   
8   046f7f2450f9c913d759e7c8bdb52fda528fb631   
9   44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5   
10  44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5   
11  44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5   
12  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
13  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
14  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
15  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
16  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
17  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
18  b63debd827dc6b2e23f4e01d9a58d9671fc80804   

                        commit_compared_with  num_dependency  \
0   a76c40a9356191fc2aa589dbd2612c0260592776          1290.0   
1   0920ddf0db0921ae0258ce1b38f5b55f9761270f           464.0   
2   5f67bd1e5b28179ddd11da500d61ae2d8ec8b8f2           114.0   
3   fea8fbba5fd9eadf3f88b91c1479290a60e6d462           143.0   
4   f5a320da7a422076bf7a401be700f36d7c2f9ec7            24.0   
5   c599a1690f7f3776885640dfd5f6755a7eceb382            22.0   
6   8703126227aba76b252f3108de760187f1982be1           354.0   
7   b17d8f1c39ce25e968d66b9d3d65d60a1a6683d6          2268.0   
8   71046d45cc7d9262b9f5ccd5c55aeb225ccf6819            22.0   
9   c1d50e371fdee18382ac813e0ec4ce23e186c14c            76.0   
10  3d3b0f64005f7d2dd7cde80a9eaf665f8df86fb6            20.0   
11  134ac982291a8d679e9cd2721a903fdeb1e1fb5b           342.0   
12  5fbf7cccd19c6f144a59cc2487e8a93636ecac0c            38.0   
13  bcdd1011f2411d634d2612f8789eedf704542591            20.0   
14  24413c1bbf675d63b07fab3ed7a4acfe1a45cf0a            20.0   
15  a128299fdb3c4fd94298071021bef17fa79f7a5f           409.0   
16  b5efb41a636154cb8bbc7c5ea3c8244090692d28          2496.0   
17  584e8503a84d508bde58b49137ed920281b3d9bf          2324.0   
18  283418b2bc079108cbe3599f06a4ebfa7211e319          1445.0   

    num_line_affected  actual_num_of_classes_touched  
0                 267                             52  
1                  32                              8  
2                  16                              6  
3                   2                              1  
4                  91                             12  
5                  13                              2  
6                  41                              6  
7                  78                             14  
8                  13                              2  
9                  41                              2  
10                 41                              4  
11                 28                              9  
12                 18                              2  
13                 41                              2  
14                 40                              2  
15               1223                              2  
16                 48                              3  
17                 19                             11  
18                107                             17

In [16]:
latest_commit_arr = []
commit_compared_with_arr = []
for row in effort_data_df.iterrows():
    sha = row[1]['latest_commit']
    commit = repo.get_commit(sha=sha)
    print(commit)
    date = commit.commit.author.date
    print(date)
    latest_commit_arr.append(date)
    
    sha = row[1]['commit_compared_with']
    commit = repo.get_commit(sha=sha)
    date = commit.commit.author.date
    commit_compared_with_arr.append(date)


Commit(sha="cbeaf8f955fff9caa5652ccc6c1393ec8b993799")
2020-09-11 21:08:20
Commit(sha="ef7c5f358e2ac8dad806952c70c7af9061a6f7af")
2020-05-17 17:52:53
Commit(sha="ef7c5f358e2ac8dad806952c70c7af9061a6f7af")
2020-05-17 17:52:53
Commit(sha="ef7c5f358e2ac8dad806952c70c7af9061a6f7af")
2020-05-17 17:52:53
Commit(sha="7334150d1da63f4fe7e256de173bdc5837022ff9")
2020-03-18 03:50:26
Commit(sha="7334150d1da63f4fe7e256de173bdc5837022ff9")
2020-03-18 03:50:26
Commit(sha="7334150d1da63f4fe7e256de173bdc5837022ff9")
2020-03-18 03:50:26
Commit(sha="7334150d1da63f4fe7e256de173bdc5837022ff9")
2020-03-18 03:50:26
Commit(sha="046f7f2450f9c913d759e7c8bdb52fda528fb631")
2020-03-08 13:36:32
Commit(sha="44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5")
2020-02-17 22:51:22
Commit(sha="44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5")
2020-02-17 22:51:22
Commit(sha="44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5")
2020-02-17 22:51:22
Commit(sha="b63debd827dc6b2e23f4e01d9a58d9671fc80804")
2019-12-31 21:39:08
Commit(sha="b63debd827dc6

In [17]:
effort_data_df['latest_commit_date'] = latest_commit_arr
effort_data_df['commit_compared_with_date'] = commit_compared_with_arr

effort_data_df

latest_commit  \
0   cbeaf8f955fff9caa5652ccc6c1393ec8b993799   
1   ef7c5f358e2ac8dad806952c70c7af9061a6f7af   
2   ef7c5f358e2ac8dad806952c70c7af9061a6f7af   
3   ef7c5f358e2ac8dad806952c70c7af9061a6f7af   
4   7334150d1da63f4fe7e256de173bdc5837022ff9   
5   7334150d1da63f4fe7e256de173bdc5837022ff9   
6   7334150d1da63f4fe7e256de173bdc5837022ff9   
7   7334150d1da63f4fe7e256de173bdc5837022ff9   
8   046f7f2450f9c913d759e7c8bdb52fda528fb631   
9   44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5   
10  44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5   
11  44124ba2a36de31ea5e6e8b4c0dc7d3b7f350df5   
12  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
13  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
14  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
15  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
16  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
17  b63debd827dc6b2e23f4e01d9a58d9671fc80804   
18  b63debd827dc6b2e23f4e01d9a58d9671fc80804   

                        commit_compared_with  num_dependency  \
0   a76c40a9356191fc2aa589dbd2612c0260592776          1290.0   
1   0920ddf0db0921ae0258ce1b38f5b55f9761270f           464.0   
2   5f67bd1e5b28179ddd11da500d61ae2d8ec8b8f2           114.0   
3   fea8fbba5fd9eadf3f88b91c1479290a60e6d462           143.0   
4   f5a320da7a422076bf7a401be700f36d7c2f9ec7            24.0   
5   c599a1690f7f3776885640dfd5f6755a7eceb382            22.0   
6   8703126227aba76b252f3108de760187f1982be1           354.0   
7   b17d8f1c39ce25e968d66b9d3d65d60a1a6683d6          2268.0   
8   71046d45cc7d9262b9f5ccd5c55aeb225ccf6819            22.0   
9   c1d50e371fdee18382ac813e0ec4ce23e186c14c            76.0   
10  3d3b0f64005f7d2dd7cde80a9eaf665f8df86fb6            20.0   
11  134ac982291a8d679e9cd2721a903fdeb1e1fb5b           342.0   
12  5fbf7cccd19c6f144a59cc2487e8a93636ecac0c            38.0   
13  bcdd1011f2411d634d2612f8789eedf704542591            20.0   
14  24413c1bbf675d63b07fab3ed7a4acfe1a45cf0a            20.0   
15  a128299fdb3c4fd94298071021bef17fa79f7a5f           409.0   
16  b5efb41a636154cb8bbc7c5ea3c8244090692d28          2496.0   
17  584e8503a84d508bde58b49137ed920281b3d9bf          2324.0   
18  283418b2bc079108cbe3599f06a4ebfa7211e319          1445.0   

    num_line_affected  actual_num_of_classes_touched  latest_commit_date  \
0                 267                             52 2020-09-11 21:08:20   
1                  32                              8 2020-05-17 17:52:53   
2                  16                              6 2020-05-17 17:52:53   
3                   2                              1 2020-05-17 17:52:53   
4                  91                             12 2020-03-18 03:50:26   
5                  13                              2 2020-03-18 03:50:26   
6                  41                              6 2020-03-18 03:50:26   
7                  78                             14 2020-03-18 03:50:26   
8                  13                              2 2020-03-08 13:36:32   
9                  41                              2 2020-02-17 22:51:22   
10                 41                              4 2020-02-17 22:51:22   
11                 28                              9 2020-02-17 22:51:22   
12                 18                              2 2019-12-31 21:39:08   
13                 41                              2 2019-12-31 21:39:08   
14                 40                              2 2019-12-31 21:39:08   
15               1223                              2 2019-12-31 21:39:08   
16                 48                              3 2019-12-31 21:39:08   
17                 19                             11 2019-12-31 21:39:08   
18                107                             17 2019-12-31 21:39:08   

   commit_compared_with_date  
0        2020-09-06 15:36:12  
1        2020-04-29 06:23:53  
2        2020-05-13 06:33:03  
3        2020-05-13 06:46:19  
4        2020-03-06 04:15:32  
5        2020-03-08 13:09:14  
6        2020-03-14 22:39:50  
7        2020-03-15 

In [24]:
try:
    os.mkdir('MoJo_1.2.1/' + project_name)
except:
    pass

groundtruth_dir = 'C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/' + project_name + '/'
#'C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/' + project_name + '/' + project_name + '_' + row[1]['version_name'] + '.txt'

groundtruth_arr = []
for root, dirs, files in os.walk(groundtruth_dir):
    #print(files)
    for file in files:
        groundtruth_full_path = groundtruth_dir + file
        groundtruth_arr.append(groundtruth_full_path)
    



for i in range(len(groundtruth_arr)-1 ,0,-1):
    print(i)
    print(groundtruth_arr[i], groundtruth_arr[i-1])
    
    # These arrays are for MoJo balancing. To have the same number of children / entities on both sides.
    arr_1 = []
    arr_2 = []
    
    # These arrays are to keep track of the changed composition for mapping?
    arr_1_changed_composition = []
    arr_2_changed_composition = []
    
    file_1 = open(groundtruth_arr[i])
    file_2 = open(groundtruth_arr[i-1])
    for line in file_1:
        line = line.split('\n')[0]
        line = line.split(' ')
        arr_1.append(line[-1])
        arr_1_changed_composition.append((line[-2], line[-1]))
    
    
    #print(to_be_added)
    
    for line in file_2:
        line = line.split('\n')[0]
        line = line.split(' ')
        arr_2.append(line[-1])
        arr_2_changed_composition.append((line[-2], line[-1]))
    
    to_be_added_2 = list(set(arr_1) - set(arr_2))
    #print(to_be_added_1)
    to_be_added_1 = list(set(arr_2) - set(arr_1))
    #print(to_be_added_2)
    
    composition_diff_2 = list(set(arr_1_changed_composition) - set(arr_2_changed_composition))
    composition_diff_1 = list(set(arr_2_changed_composition) - set(arr_1_changed_composition))
    composition_diff = composition_diff_1 + composition_diff_2
    #print(composition_diff)
    
    
    
    file_1 = open(groundtruth_arr[i])
    file_2 = open(groundtruth_arr[i-1])
    temp_1 = open('C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1/temp_1.txt', 'w')
    for line in file_1:
        temp_1.write(line)
    for element in to_be_added_1:
        temp_1.write('contain ' + element + ' ' + element + '\n')
    temp_1.close()
    
    temp_2 = open('C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1/temp_2.txt', 'w')
    for line in file_2:
        temp_2.write(line)
    for element in to_be_added_2:
        temp_2.write('contain ' + element + ' ' + element + '\n')
    temp_2.close()
    
    file_1.close()
    file_2.close()
    
    f = open('C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1/' + project_name + '/' + project_name + '_results.txt', 'a')
    identifier = str(groundtruth_arr[i].split('/')[-1].replace('.txt', '')) + ',' + str(groundtruth_arr[i-1].split('/')[-1].replace('.txt', '')) + '\n'
    print(identifier)
    f.write(str(identifier))
    f.write(str(composition_diff) + '\n')
    #print(str(groundtruth_arr[i].split('_')[-1].replace('.txt', '')))
    #print(current_project[current_project['version_name'] == str(groundtruth_arr[i].split('_')[-1].replace('.txt', ''))]['timestamp_diff_hours'].values[0])
    time_taken = current_project[current_project['version_name'] == str(groundtruth_arr[i].split('_')[-1].replace('.txt', ''))]['timestamp_diff_hours'].values[0]
    f.write('Hours taken:' + str(time_taken) + '\n')
    f.close()
    
    command = 'cd C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1 & ' + 'java MoJo ' + 'temp_1.txt' + ' ' + 'temp_2.txt' + ' >> ' + project_name + '/' + project_name + '_results.txt'
    print(command)
    os.system(command)
    
    os.remove('C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1/temp_1.txt')
    os.remove('C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1/temp_2.txt')
    

9
C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/okhttp/okhttp_parent-4.9.1.txt C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/okhttp/okhttp_parent-4.9.0.txt
okhttp_parent-4.9.1,okhttp_parent-4.9.0

cd C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1 & java MoJo temp_1.txt temp_2.txt >> okhttp/okhttp_results.txt
8
C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/okhttp/okhttp_parent-4.9.0.txt C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/okhttp/okhttp_parent-4.8.1.txt
okhttp_parent-4.9.0,okhttp_parent-4.8.1

cd C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1 & java MoJo temp_1.txt temp_2.txt >> okhttp/okhttp_results.txt
7
C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/okhttp/okhttp_parent-4.8.1.txt C:/Users/tanji/Desktop/SoftwareRemodularization/groundtruth/okhttp/okhttp_parent-4.8.0.txt
okhttp_parent-4.8.1,okhttp_parent-4.8.0

cd C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1 & java MoJo t

In [ ]:
## Get all commits

repo = g.get_repo('apache/zookeeper')

for release in repo.get_commits():
    #print(release.commit.sha)
    commit = repo.get_commit(sha=release.commit.sha)
    print(commit.commit.author.date)
    #print(commit.commit.message)

In [31]:
## Get all tags

repo = g.get_repo('apache/zookeeper')

for release in repo.get_tags():
    #print(release.commit.sha)
    commit = repo.get_commit(sha=release.commit.sha)
    print(commit.commit.author.date)
    #print(commit.commit.message)

2019-01-22 14:37:29
[maven-release-plugin] prepare release zookeeper-\
2021-03-17 09:42:11
Prepared 3.7.0
2021-03-17 09:42:11
Prepared 3.7.0
2021-01-24 19:05:00
Prepared 3.7.0
2021-01-19 09:36:44
Prepared 3.7.0
2021-04-08 16:27:50
Prepared 3.6.3
2021-04-08 16:27:50
Prepared 3.6.3
2021-04-04 10:47:19
Prepared 3.6.3
2021-04-01 09:20:13
Prepared 3.6.3
2020-09-04 12:34:41
Prepared 3.6.2
2020-09-04 12:34:41
Prepared 3.6.2
2020-08-31 14:47:18
Prepared 3.6.2
2020-04-21 14:57:00
Prepared 3.6.1
2020-04-21 14:57:00
Prepared 3.6.1
2020-04-15 15:56:05
Prepared 3.6.1
2020-02-25 14:17:17
Prepared 3.6.0
2020-02-25 14:17:17
Prepared 3.6.0
2020-02-18 16:52:00
Prepared 3.6.0
2020-02-05 19:03:11
Prepared 3.6.0
2020-02-01 13:26:45
Prepared 3.6.0
2020-01-11 13:21:49
Prepared 3.6.0
2021-01-06 19:46:31
Preparing for release 3.5.9
2021-01-06 19:46:31
Preparing for release 3.5.9
2021-01-06 16:26:38
Preparing for release 3.5.9
2020-11-26 14:33:54
Preparing for release 3.5.9
2020-05-04 14:24:46
Preparing for rel

2019-03-06 03:32:11
Exclude spotbugs annotations jar from the release

Fix for 3.4.14-rc4: exclude `spotbugs-annotations` jar from the distribution.

Author: Andor Molnar <andor@apache.org>

Reviewers: phunt@apache.org

Closes #841 from anmolnar/fix_rc_exclude_spotbugsjar

Change-Id: Ie4a36613161e103fc2c50690281fa26c90f48d1b
(cherry picked from commit 372e713a9d2d9264417313e5d68e9437ffddd0f5)
Signed-off-by: Patrick Hunt <phunt@apache.org>
2019-02-27 15:48:59
Fixed version numbers in pom.xml files
2019-02-20 12:01:26
ZOOKEEPER-1815: Tolerate incorrectly set system hostname in tests (3.4)

Inspired by the following commit: https://github.com/apache/zookeeper/commit/23852655a6d41f675b8a9cca66387fca9bfe4e12

in order to fix build problems on H31 Jenkins slave. Infra reported that nothing has been changed in name resolution, but the patch still looks reasonable and hopefully fix the JMX connection problem.

This "backport" is JMX-only and doesn't try to fully backport the original patch.

A

KeyboardInterrupt: 

In [5]:
response = requests.get("https://api.github.com/repos/apache/zookeeper/stats/contributors")

In [6]:
print(response)

<Response [200]>


In [7]:
response.json()

[{'total': 2,
  'weeks': [{'w': 1193529600, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1194134400, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1194739200, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1195344000, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1195948800, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1196553600, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1197158400, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1197763200, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1198368000, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1198972800, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1199577600, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1200182400, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1200787200, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1201392000, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1201996800, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1202601600, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1203206400, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1203811200, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1204416000, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1205020800, 'a': 0, 'd': 0, 'c': 0},
   {'w': 1205625600, 'a': 0, 'd': 0, 'c': 0},
   {'w': 12

In [9]:
print(len(response.json()))

100


In [ ]:
total_weeks = None

for element in response.json():
    if total_weeks is None:
        total_weeks = []
        for week in element['weeks']:
            total_weeks.append(week['w'], week['a'], week['d'], week['c'])
    else:
        for week in element['weeks']:
            total_weeks.append(week['w'], week['a'], week['d'], week['c'])
    

In [15]:
response_2 = requests.get("https://api.github.com/repos/apache/spark/stats/contributors")

In [16]:
print(len(response_2.json()))

100


In [16]:
file = open('C:/Users/tanji/Desktop/SoftwareRemodularization/MoJo_1.2.1/dropwizard/dropwizard_results.txt')
for line in file:
    print(line)
    print(' ')
file.close()

dropwizard_v2.1.0-beta.1,dropwizard_v2.0.9

 
MoJo(temp_1.txt,temp_2.txt) = 26

 


 
MoJo(temp_2.txt,temp_1.txt) = 26

 
The Mojo value is 26

 
dropwizard_v2.0.9,dropwizard_v2.0.8

 
MoJo(temp_1.txt,temp_2.txt) = 5

 


 
MoJo(temp_2.txt,temp_1.txt) = 5

 
The Mojo value is 5

 
dropwizard_v2.0.8,dropwizard_v2.0.7

 
MoJo(temp_1.txt,temp_2.txt) = 0

 


 
MoJo(temp_2.txt,temp_1.txt) = 0

 
The Mojo value is 0

 
dropwizard_v2.0.7,dropwizard_v2.0.6

 
MoJo(temp_1.txt,temp_2.txt) = 0

 


 
MoJo(temp_2.txt,temp_1.txt) = 0

 
The Mojo value is 0

 
dropwizard_v2.0.6,dropwizard_v2.0.5

 
MoJo(temp_1.txt,temp_2.txt) = 0

 


 
MoJo(temp_2.txt,temp_1.txt) = 0

 
The Mojo value is 0

 
dropwizard_v2.0.5,dropwizard_v2.0.4

 
MoJo(temp_1.txt,temp_2.txt) = 0

 


 
MoJo(temp_2.txt,temp_1.txt) = 0

 
The Mojo value is 0

 
dropwizard_v2.0.4,dropwizard_v2.0.3

 
MoJo(temp_1.txt,temp_2.txt) = 0

 


 
MoJo(temp_2.txt,temp_1.txt) = 0

 
The Mojo value is 0

 
dropwizard_v2.0.3,dropwizard_v2.0.21

